import requests
import re
from IPython.display import display, HTML
from pandas import DataFrame

# 列表页集合
listPages = []

# 抓取讲师列表页首页HTML
res = requests.get('http://finance.jxufe.edu.cn/news-list-jiangshi.html')
res.encoding = 'utf-8'
listPages.append(res.text)

# 获取讲师列表页尾页索引
pageEnd = int(re.findall(r"\d+(?=[^\d]+尾页)", res.text)[0])

# 首页已经爬取，所以接着需要从第2页爬取
pageIndex = 2
while pageIndex <= pageEnd:
    res = requests.get('http://finance.jxufe.edu.cn/news-list-jiangshi-' + str(pageIndex) + '.html')
    res.encoding = 'utf-8'
    listPages.append(res.text)
    pageIndex = pageIndex + 1

# 列表页全部爬取之后，获取全部讲师链接
jiangShiUrls = []
for listPage in listPages:
    jiangShiUrls = set(jiangShiUrls) ^ set(re.findall(r"http://finance\.jxufe\.edu\.cn/news-show-\d+\.html", listPage))

# 根据全部讲师链接，获取全部讲师页面
jiangShiPages = []
for jiangShiUrl in jiangShiUrls:
    res = requests.get(jiangShiUrl)
    res.encoding = 'utf-8'

    # 截取有用部分代码
    jiangShiPage = re.findall(r"ne_main_R[^>]*>.*", res.text)[0] if re.search(r"ne_main_R[^>]+>.*", res.text) else ''
    if jiangShiPage == '':
        continue

    # 替换全部空格换行空字符
    jiangShiPage = re.sub(r"\s|&nbsp;", '', res.text)

    jiangShiPages.append({'url': jiangShiUrl, 'html': jiangShiPage})

jiang_shi = []

for jiangShi in jiangShiPages:
    jiangShiPage = jiangShi['html']

    teacher = {'url': jiangShi['url']}
    teacher['姓名'] = re.findall(r"(?<=姓名<\/strong>：)[^<]+", jiangShiPage)[0] if re.search(r"(?<=姓名<\/strong>：)[^<]+", jiangShiPage) else ''
    teacher['性别'] = re.findall(r"男|女", jiangShiPage)[0] if re.search(r"男|女", jiangShiPage) else ''
    teacher['政治面貌'] = re.findall(r"(?<=政治面貌<\/strong>：)[^<]+", jiangShiPage)[0] if re.search(r"(?<=政治面貌<\/strong>：)[^<]+", jiangShiPage) else ''
    teacher['毕业院校'] = re.findall(r"(?<=毕业院校<\/strong>：)[^<]+", jiangShiPage)[0] if re.search(r"(?<=毕业院校<\/strong>：)[^<]+", jiangShiPage) else ''
    teacher['毕业专业'] = re.findall(r"(?<=毕业专业<\/strong>：)[^<]+", jiangShiPage)[0] if re.search(r"(?<=毕业专业<\/strong>：)[^<]+", jiangShiPage) else ''
    teacher['联系方式'] = re.findall(r"(?<=邮箱<\/strong>：)[^<]+", jiangShiPage)[0] if re.search(r"(?<=邮箱<\/strong>：)[^<]+", jiangShiPage) else ''

    if teacher['姓名'] == '':
        s = re.findall(r"(?<=姓名)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage)[0] if re.search(r"(?<=姓名)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage) else ''
        if s != '':
            teacher['姓名'] = re.findall(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s)[0] if re.search(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s) else ''

            if len(teacher['姓名']) == 1:
                m = re.findall(r"(?<=姓名)[^：]*：([\u4e00-\u9fa5])+(<[^<|^>]*>)*([\u4e00-\u9fa5])+", jiangShiPage)[0]
                s = ''.join(m)
                s = re.sub(r"(<[^<|^>]*>)*", '', s)
                teacher['姓名'] = s

    if teacher['姓名'] == '':
        m = re.findall(r"姓(<[^<|^>]*>)*名(<[^<|^>]*>)*：*(<[^<|^>]*>)*([\u4e00-\u9fa5]+)", jiangShiPage)[0]
        s = ''.join(m)
        s = re.sub(r"(<[^<|^>]*>)*", '', s)
        teacher['姓名'] = s

    if teacher['政治面貌'] == '':
        s = re.findall(r"(?<=政治面貌)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage)[0] if re.search(r"(?<=政治面貌)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage) else ''
        if s != '':
            teacher['政治面貌'] = re.findall(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s)[0] if re.search(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s) else ''

    if teacher['毕业院校'] == '':
        s = re.findall(r"(?<=毕业院校)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage)[0] if re.search(r"(?<=毕业院校)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage) else ''
        if s != '':
            teacher['毕业院校'] = re.findall(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s)[0] if re.search(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s) else ''

    if teacher['毕业院校'] == '':
        r = r"毕(<[^<|^>]*>)*业(<[^<|^>]*>)*院(<[^<|^>]*>)*校(<[^<|^>]*>)*：*(<[^<|^>]*>)*([\u4e00-\u9fa5]+)(</?[^<|^>]*>)*</p[^>]*>"
        m = re.findall(r, jiangShiPage)[0] if re.search(r, jiangShiPage) else []
        s = ''.join(m)
        s = re.sub(r"(</?[^<|^>]*>)*", '', s)
        teacher['毕业院校'] = s

    if teacher['毕业专业'] == '':
        s = re.findall(r"(?<=毕业专业)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage)[0] if re.search(r"(?<=毕业专业)[^：]*：[\u4e00-\u9fa5]+", jiangShiPage) else ''
        if s != '':
            teacher['毕业专业'] = re.findall(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s)[0] if re.search(r"(?<=：)[^：]*[\u4e00-\u9fa5]+", s) else ''

    if teacher['联系方式'] == '':
        r = r"([A-Z|a-z|0-9]+([_|\.][A-Z|a-z|0-9]+)*@([A-Z|a-z|0-9\-]+\.)+[A-Z|a-z]{2,20})"
        m = re.findall(r, jiangShiPage)[0] if re.search(r, jiangShiPage) else []
        s = m[0]
        teacher['联系方式'] = s

    jiang_shi.append(teacher)

# print(jiang_shi)

# data = {'姓名': [], '性别': [], '政治面貌': [], '毕业院校': [], '毕业专业': [], '联系方式': [], '来源': []}
data = {'姓名': [], '性别': [], '政治面貌': [], '毕业院校': [], '毕业专业': [], '联系方式': []}

for teacher in jiang_shi:
    data['姓名'].append(teacher['姓名'])
    data['性别'].append(teacher['性别'])
    data['政治面貌'].append(teacher['政治面貌'])
    data['毕业院校'].append(teacher['毕业院校'])
    data['毕业专业'].append(teacher['毕业专业'])
    data['联系方式'].append(teacher['联系方式'])
    # data['来源'].append(teacher['url'])

df1 = DataFrame(data)

display(HTML(df1.to_html()))
